## Preparación de un dataset

Descargamos el dataset y lo preparamos para el entrenamiento. En el caso de ejemplo, usaremos toxic-teenage-relationships, que son frases que describen si un comporamiento es tóxico o sano. Tienen una campo de texto y un campo de etiqueta, que vale 1 si es tóxico y 0 si no lo es. Acumula 267 ejemplos de entrenamiento y 66 para testear.

In [1]:
from datasets import load_dataset
data_files = {"train": "train.csv", "test": "test.csv"}
dataset = load_dataset("toxic-teenage-relationships", data_files=data_files, sep=";")
dataset['train'][102]

{'label': 1, 'text': 'Me mira mal por mi forma de vestir'}

Una vez cargado el dataset, se crea un tokenizador para procesar el texto e incluir una estrategia para el padding y el truncamiento. Par poder procesar el dataset en un solo paso, se utiliza el método dataset.map para preprocesar todo el dataset.



In [2]:

from transformers import AutoTokenizer
#el modelo a utilizar es BETo
tokenizer = AutoTokenizer.from_pretrained("dccuchile/bert-base-spanish-wwm-cased")


def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)


tokenized_datasets = dataset.map(tokenize_function, batched=True)


In [3]:
train_dataset = tokenized_datasets["train"]
eval_dataset = tokenized_datasets["test"]

## Fine-tuning usando Trainer

La clase trainer de Transformers permite entrenar modelos de transformers. La API del Trainer soporta varias opciones de entrenamiento y características como logging, gradient accumulation y mixed preccision

In [4]:
from transformers import AutoModelForSequenceClassification

#Hay dos categorías, así que ponemos 2 etiquetas (0 sano 1 tóxico)
model = AutoModelForSequenceClassification.from_pretrained("dccuchile/bert-base-spanish-wwm-cased", num_labels=2)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at dccuchile/bert-base-spanish-wwm-cased and are newly initialized: ['classifier.bias', 'bert.pooler.dense.weight', 'classifier.weight', 'bert.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


## Hiperparámetros de entrenamiento

Ahora se crea una clase TrainingArguments que contiene todos los hiperparámetros que se pueden ajustar. 
Empezamos con los hiperparámetros de entrenamiento por defecto, pero tendremos que ajustarlos para encontrar la configuración óptima.


In [5]:
#Para poder evitar el overfitting, voy a añadir la clase earlystopping en el momento que se observe
#que la pérdida se incrementa en dos epoch
from transformers import EarlyStoppingCallback
early_stop=EarlyStoppingCallback(early_stopping_patience=2)

In [6]:
from transformers import TrainingArguments
from transformers import DataCollatorWithPadding
from transformers import AdamW
# para controlar las métricas de evaluación durante el fine-tuning
# vamos a añadir que elija el mejor modelo al final, usamos load_best_model_at_end que cogerá eval_loss para evaluar
# para que se fije en el valor de loss como la mejor métrica, hay que poner greater_is_better a false.
#vamos a poner el número de epoch a 10 y el del batch a 8

training_args = TrainingArguments(output_dir="BETo-t-MMG",
                                  num_train_epochs=10,
                                  per_device_train_batch_size=8,
                                  per_device_eval_batch_size=8,
                                 load_best_model_at_end=True,
                                 greater_is_better=False,
                                 evaluation_strategy="epoch",
                                 save_strategy="epoch")
#optimizador 
optimizer=AdamW(model.parameters(),lr=5e-5)
#añado el data Collator, que en este caso va a ser parte del trainer.
#este es el indicado específicamente para tareas de clasificación de texto, agrupa y preprocesa
#para que todos los ejemplos de entrada en lotes tengan la misma longitud además del tokenizdor
#agrupación en lotes y creación de mapas de atención.
#usando la función .map, no es estrictamente necesario pero así se combinan las características
#adicionales del texto antes de pasarle el datacollator.
data_collator = DataCollatorWithPadding(tokenizer)

/home/mmartinez/anaconda3/envs/TFM/lib/python3.8/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


## Métricas

El Trainer no evalúa automátiamentee el rendimiento, hay que pasarle una función para calcular y hacer un reporte de las métricas. En Datasets hay una función, accuracy, que se puede cargar con load_metric. 
Antes hay que instalar scikit-learn

In [7]:
pip install scikit-learn

Note: you may need to restart the kernel to use updated packages.


In [8]:
import numpy as np
from datasets import load_metric

metric = load_metric("accuracy")

/tmp/ipykernel_3270586/2607597888.py:4: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("accuracy")


Se define la función compute_metrics para calcular el accuracy de las predicciones hechas. Antes de pasar las predicciones a compute, hay que convertir las predicciones a logits (los modelos de Transformers devuelven logits).

In [9]:
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)

## Trainer

Ahora es el momento de crear el objeto Trainer con el modelo, argumentos de entrenamiento, datasets de entrenamiento y de prueba, y función de evaluación:

In [12]:
from transformers import Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    data_collator=data_collator,
    optimizers=(optimizer, None),
    compute_metrics=compute_metrics,
    callbacks=[early_stop],
)

Y se aplica fine-tunning con train

In [13]:
trainer.train()

You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=102, training_loss=0.33487387264476104, metrics={'train_runtime': 88.4219, 'train_samples_per_second': 30.309, 'train_steps_per_second': 3.845, 'total_flos': 211541288509440.0, 'train_loss': 0.33487387264476104, 'epoch': 3.0})

Imprimo el loss y el accuracy

In [15]:
#creo una función para imprimir los resultados de una formá más visual
def print_results(title, results):
    print(title)
    for key, value in results.items():
        print(f"{key}. {value}")
        
train_result = trainer.evaluate(train_dataset)
print_results("Resultados del conjunto de train",train_result)
eval_result = trainer.evaluate(eval_dataset)
print_results("Resultados del conjunto de test",eval_result)

Resultados del conjunto de train
eval_loss. 0.19221480190753937
eval_accuracy. 0.9440298507462687
eval_runtime. 9.8909
eval_samples_per_second. 27.095
eval_steps_per_second. 3.437
epoch. 3.0
Resultados del conjunto de test
eval_loss. 0.4598655700683594
eval_accuracy. 0.803030303030303
eval_runtime. 2.4345
eval_samples_per_second. 27.11
eval_steps_per_second. 3.697
epoch. 3.0


# Guardando el modelo

Para Guardarlo, utilizamos esl método save_model

In [16]:
trainer.save_model()

In [17]:
trainer.create_model_card()